# Algorithms

[Click here to run this chapter on Colab](https://colab.research.google.com/github/AllenDowney/DSIRP/blob/main/notebooks/algorithms.ipynb)

## Searching for anagrams

In this notebook we'll implement algorithms for two tasks:

* Testing a pair of words to see if they are anagrams of each other, that is, if you can rearrange the letters in one word to spell the other.

* Searching a list of words for all pairs that are anagrams of each other.

There is a point to these examples, which I will explain at the end.

**Exercise 1:** Write a function that takes two words and returns `True` if they are anagrams. Test your function with the examples below.

In [1]:
def is_anagram(word1, word2):
    return False

In [2]:
# Solution

def is_anagram1(word1, word2):
    t = list(word2)
    for letter in word1:
        if letter not in t:
            return False
        t.remove(letter)
    return len(t) == 0

In [3]:
# Solution

from collections import Counter

def is_anagram2(word1, word2):
    return Counter(word1) == Counter(word2)

In [4]:
# Solution

def is_anagram3(word1, word2):
    return sorted(word1) == sorted(word2)

In [5]:
is_anagram('tachymetric', 'mccarthyite') # True

False

In [6]:
is_anagram('post', 'top') # False, letter not present

False

In [7]:
is_anagram('pott', 'top') # False, letter present but not enough copies

False

In [8]:
is_anagram('top', 'post') # False, letters left over at the end

False

In [9]:
is_anagram('topss', 'postt') # False

False

**Exercise 2:** Use `timeit` to see how fast your function is for these examples:

In [10]:
%timeit is_anagram('tops', 'spot')

50.8 ns ± 0.779 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)


In [11]:
%timeit is_anagram('tachymetric', 'mccarthyite')

49.9 ns ± 3.99 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)


How can we compare algorithms running on different computers?

## Searching for anagram pairs

**Exercise 3:** Write a function that takes a word list and returns a list of all anagram pairs.

In [12]:
short_word_list = ['proudest', 'stop', 'pots', 'tops', 'sprouted']

In [13]:
def all_anagram_pairs(word_list):
    return []

In [14]:
# Solution

def all_anagram_pairs(word_list):
    """Finds all anagram pairs
    """
    res = []
    for i, word1 in enumerate(word_list):
        for word2 in word_list[i+1:]:
            if is_anagram(word1, word2):
                res.append((word1, word2))
    return res  

In [15]:
all_anagram_pairs(short_word_list)

[]

The following cell downloads a file containing a list of English words.

In [16]:
from os.path import basename, exists

def download(url):
    filename = basename(url)
    if not exists(filename):
        from urllib.request import urlretrieve
        local, _ = urlretrieve(url, filename)
        print('Downloaded ' + local)
    
download('https://github.com/AllenDowney/DSIRP/raw/main/american-english')

The following function reads a file and returns a set of words (I used a set because after we convert words to lower case, there are some repeats.)

In [17]:
def read_words(filename):
    """Read lines from a file and split them into words."""
    res = set()
    for line in open(filename):
        for word in line.split():
            res.add(word.strip().lower())
    return res

In [18]:
word_list = read_words('american-english')
len(word_list)

100781

**Exercise 4:** Loop through the word list and print all words that are anagrams of `stop`.

In [19]:
# Solution

for word in word_list:
    if is_anagram(word, 'stop'):
        print(word)

Now run `all_anagram_pairs` with the full `word_list`:

In [20]:
# pairs = all_anagram_pairs(word_list)

**Exercise 5:** While that's running, let's estimate how long it's going to take.

In [21]:
# Solution 

print(500e-9 * 1e5 * 1e5 / 60, 'minutes') 

83.33333333333333 minutes


## A better algorithm

**Exercise 6:** Write a better algorithm! Hint: make a dictionary. How much faster is your algorithm?

In [22]:
def all_anagram_lists(word_list):
    """Finds all anagrams in a list of words.

    word_list: sequence of strings
    """
    return {}

In [23]:
# Solution

def all_anagram_lists(word_list):
    """Finds all anagrams in a list of words.

    word_list: sequence of strings
    
    returns: a map from a tuple of letters to a list of its anagrams.
    """
    d = {}
    for word in word_list:
        t = tuple(sorted((word)))

        if t not in d:
            d[t] = [word]
        else:
            d[t].append(word)
    return d

In [24]:
%time anagram_map = all_anagram_lists(word_list)

CPU times: user 173 ms, sys: 8.02 ms, total: 181 ms
Wall time: 180 ms


In [25]:
len(anagram_map)

93406

In [26]:
# Solution

500e-9 * 1e5 * 1e5 / 200e-3

25000.0

## Summary

What is the point of the examples in this notebook?

* The different versions of `is_anagram` show that, when inputs are small, it is hard to say which algorithm will be the fastest. It often depends on details of the implementation. Anyway, the differences tend to be small, so it might not matter much in practice.

* The different algorithms we used to search for anagram pairs show that, when inputs are large, we can often tell which algorithm will be fastest. And the difference between a fast algorithm and a slow one can be huge!

## Exercises

Before you work on these exercises, you might want to read the Python [Sorting How-To](https://docs.python.org/3/howto/sorting.html). It uses `lambda` to define an anonymous function, which [you can read about here](https://www.w3schools.com/python/python_lambda.asp).

**Exercise 7:**
Make a dictionary like `anagram_map` that contains only keys that map to a list with more than one element. You can use a `for` loop to make a new dictionary, or a [dictionary comprehension](https://www.freecodecamp.org/news/dictionary-comprehension-in-python-explained-with-examples/).

In [27]:
# Solution

anagram_map2 = {key: value for (key, value) in anagram_map.items()
                if len(value) > 1}
len(anagram_map2)

5872

**Exercise 8:**
Find the longest word with at least one anagram. Suggestion: use the `key` argument of `sort` or `sorted` ([see here](https://stackoverflow.com/questions/8966538/syntax-behind-sortedkey-lambda)).

In [28]:
# Solution

it = sorted(anagram_map2.items(), key=lambda t: len(t[0]), reverse=True)
for key, value in it[:10]:
    print(value)

["impressiveness's", "permissiveness's"]
["certification's", "rectification's"]
['tablespoonfuls', 'tablespoonsful']
['rectifications', 'certifications']
["conversation's", "conservation's"]
["amphitheatre's", "amphitheater's"]
['permissiveness', 'impressiveness']
['perfectionism', 'imperfections']
['amphitheaters', 'amphitheatres']
["edification's", "deification's"]


**Exercise 9:**
Find the largest list of words that are anagrams of each other.

In [29]:
# Solution

it = sorted(anagram_map2.items(), key=lambda t: len(t[1]), reverse=True)
for key, value in it[:10]:
    print(value)

['stale', 'tales', 'stael', 'least', 'teals', 'tesla', 'steal', 'slate']
['traces', 'recast', 'caster', 'caters', 'reacts', 'carets', 'crates']
['pares', 'spear', 'pears', 'parse', 'reaps', 'rapes', 'spare']
['leaps', 'pales', 'peals', 'lapse', 'sepal', 'pleas']
['post', 'spot', 'stop', 'pots', 'opts', 'tops']
['padres', 'spread', 'parsed', 'rasped', 'drapes', 'spared']
['costar', 'castor', 'castro', 'actors', 'scrota', 'croats']
['caret', 'react', 'cater', 'trace', 'recta', 'crate']
['teaks', 'keats', 'stake', 'steak', 'takes', 'skate']
['sale', 'seal', 'ales', 'leas', 'lesa', 'elsa']


**Exercise 10:**
Write a function that takes an integer `word_length` and finds the longest list of words with the given length that are anagrams of each other.

In [30]:
# Solution

def longest_list(anagram_map, word_length):
    subset = {key: value for (key, value) in anagram_map.items()
              if len(key) == word_length}
    t = sorted(subset.items(), key=lambda t: len(t[1]), reverse=True)
    for key, value in t[:10]:
        print(value)

In [31]:
# Solution

longest_list(anagram_map2, 8)

['tangiers', 'tasering', 'rangiest', 'ingrates', 'angriest', 'gantries']
['resident', 'dniester', 'inserted', 'nerdiest', 'trendies']
["elanor's", "loaner's", "lorena's", "lenora's", "elnora's"]
["lustre's", "luster's", "result's", "ulster's", "rustle's"]
['triangle', 'relating', 'integral', 'altering', 'alerting']
['strainer', 'trainers', 'retrains', 'restrain', 'terrains']
["corset's", "escort's", "sector's", "cortes's"]
["torres's", "resort's", "sorter's", "roster's"]
["armani's", "airman's", "marian's", "marina's"]
["phrase's", "sherpa's", "sharpe's", "seraph's"]


**Exercise 11:**
At this point we have a data structure that contains lists of words that are anagrams, but we have not actually enumerated all pairs.
Write a function that takes `anagram_map` and returns a list of all anagram pairs.
How many are there?

In [32]:
# Solution

def enumerate_pairs(anagram_map):
    res = []
    for key, value in anagram_map.items():
        for i in range(len(value)):
            for j in range(i+1, len(value)):
                res.append((value[i], value[j]))
    return res

In [33]:
# Solution

pair_list = enumerate_pairs(anagram_map)

In [34]:
# Solution

len(pair_list)

9396

In [35]:
# Solution

pair_list[:20]

[('roger', 'regor'),
 ('roger', 'reorg'),
 ('regor', 'reorg'),
 ('strewing', 'wresting'),
 ("tar's", "rat's"),
 ("tar's", "art's"),
 ("rat's", "art's"),
 ('ends', 'dens'),
 ('ends', 'send'),
 ('dens', 'send'),
 ("enigma's", "gamine's"),
 ('leaps', 'pales'),
 ('leaps', 'peals'),
 ('leaps', 'lapse'),
 ('leaps', 'sepal'),
 ('leaps', 'pleas'),
 ('pales', 'peals'),
 ('pales', 'lapse'),
 ('pales', 'sepal'),
 ('pales', 'pleas')]

*Data Structures and Information Retrieval in Python*

Copyright 2021 Allen Downey

License: [Creative Commons Attribution-NonCommercial-ShareAlike 4.0 International](https://creativecommons.org/licenses/by-nc-sa/4.0/)